## Featurizer Class

In [1]:
import torch
from simplediff import diff

## FOLLOWING CODE IS TAKEN FROM GITHUB CODE OF NEUTRALIZING BIAS
## https://github.com/rpryzant/neutralizing-bias

# The Featurizer class and any depencies are added in this code block

# from https://spacy.io/api/annotation#section-dependency-parsing
RELATIONS = [
    'det', 'amod', 'nsubj', 'prep', 'pobj', 'ROOT', 
    'attr', 'punct', 'advmod', 'compound', 'acl', 'agent', 
    'aux', 'ccomp', 'dobj', 'cc', 'conj', 'appos', 'nsubjpass', 
    'auxpass', 'poss', 'nummod', 'nmod', 'relcl', 'mark', 
    'advcl', 'pcomp', 'npadvmod', 'preconj', 'neg', 'xcomp', 
    'csubj', 'prt', 'parataxis', 'expl', 'case', 'acomp', 'predet',
    'quantmod', 'dep', 'oprd', 'intj', 'dative', 'meta', 'csubjpass', 
    '<UNK>'
]
REL2ID = {x: i for i, x in enumerate(RELATIONS)}

# from https://spacy.io/api/annotation#section-pos-tagging
POS_TAGS = [
    'DET', 'ADJ', 'NOUN', 'ADP', 'NUM', 'VERB', 'PUNCT', 'ADV', 
    'PART', 'CCONJ', 'PRON', 'X', 'INTJ', 'PROPN', 'SYM',
    '<UNK>'
]
POS2ID = {x: i for i, x in enumerate(POS_TAGS)}

import nltk
import numpy as np
from nltk.parse.stanford import StanfordDependencyParser

class Featurizer:

    def __init__(self, tok2id={}, pad_id=0, lexicon_feature_bits=1):
        self.tok2id = tok2id
        self.id2tok = {x: tok for tok, x in tok2id.items()}
        self.pad_id = pad_id

        self.pos2id = POS2ID
        self.rel2id = REL2ID
        
        # Ensure that these files are present, they can be found in the above GitHub link
        self.lexicons = {
            'assertives': self.read_lexicon('lexicons/assertives_hooper1975.txt'),
            'entailed_arg': self.read_lexicon('lexicons/entailed_arg_berant2012.txt'),
            'entailed': self.read_lexicon('lexicons/entailed_berant2012.txt'), 
            'entailing_arg': self.read_lexicon('lexicons/entailing_arg_berant2012.txt'), 
            'entailing': self.read_lexicon('lexicons/entailing_berant2012.txt'), 
            'factives': self.read_lexicon('lexicons/factives_hooper1975.txt'),
            'hedges': self.read_lexicon('lexicons/hedges_hyland2005.txt'),
            'implicatives': self.read_lexicon('lexicons/implicatives_karttunen1971.txt'),
            'negatives': self.read_lexicon('lexicons/negative_liu2005.txt'),
            'positives': self.read_lexicon('lexicons/positive_liu2005.txt'),
            'npov': self.read_lexicon('lexicons/npov_lexicon.txt'),
            'reports': self.read_lexicon('lexicons/report_verbs.txt'),
            'strong_subjectives': self.read_lexicon('lexicons/strong_subjectives_riloff2003.txt'),
            'weak_subjectives': self.read_lexicon('lexicons/weak_subjectives_riloff2003.txt')
        }
        self.lexicon_feature_bits = lexicon_feature_bits


    def get_feature_names(self):

        lexicon_feature_names = list(self.lexicons.keys())
        context_feature_names = [x + '_context' for x in lexicon_feature_names]
        pos_names = list(list(zip(*sorted(self.pos2id.items(), key=lambda x: x[1])))[0])
        rel_names = list(list(zip(*sorted(self.rel2id.items(), key=lambda x: x[1])))[0])

        return lexicon_feature_names + context_feature_names + pos_names + rel_names        

    def read_lexicon(self, fp):
        out = set([
            l.strip() for l in open(fp, errors='ignore') 
            if not l.startswith('#') and not l.startswith(';')
            and len(l.strip().split()) == 1
        ])
        return out


    def lexicon_features(self, words, bits=2):
        assert bits in [1, 2]
        if bits == 1:
            true = 1
            false = 0
        else:
            true = [1, 0]
            false = [0, 1]
    
        out = []
        for word in words:
            out.append([
                true if word in lexicon else false 
                for _, lexicon in self.lexicons.items()
            ])
        out = np.array(out)

        if bits == 2:
            out = out.reshape(len(words), -1)

        return out


    def context_features(self, lex_feats, window_size=2):
        out = []
        nwords = lex_feats.shape[0]
        nfeats = lex_feats.shape[1]
        for wi in range(lex_feats.shape[0]):
            window_start = max(wi - window_size, 0)
            window_end = min(wi + window_size + 1, nwords)

            left = lex_feats[window_start: wi, :] if wi > 0 else np.zeros((1, nfeats))
            right = lex_feats[wi + 1: window_end, :] if wi < nwords - 1 else np.zeros((1, nfeats))

            out.append((np.sum(left + right, axis=0) > 0).astype(int))

        return np.array(out)


    def features(self, id_seq, rel_ids, pos_ids):
        if self.pad_id in id_seq:
            pad_idx = id_seq.index(self.pad_id)
            pad_len = len(id_seq[pad_idx:])
            id_seq = id_seq[:pad_idx]
            rel_ids = rel_ids[:pad_idx]
            pos_ids = pos_ids[:pad_idx]
        else:
            pad_len = 0

        toks = [self.id2tok[x] for x in id_seq]
        # build list of [word, [tok indices the word came from]]
        words = []
        word_indices = []
        for i, tok in enumerate(toks):
            if tok.startswith('##'):
                words[-1] += tok.replace('##', '')
                word_indices[-1].append(i)
            else:
                words.append(tok)
                word_indices.append([i])

        # get expert features
        lex_feats = self.lexicon_features(words, bits=self.lexicon_feature_bits)
        context_feats = self.context_features(lex_feats)
        expert_feats = np.concatenate((lex_feats, context_feats), axis=1)
        # break word-features into tokens
        feats = np.concatenate([
            np.repeat(np.expand_dims(word_vec, axis=0), len(indices), axis=0) 
            for (word_vec, indices) in zip(expert_feats, word_indices)
        ], axis=0)

        # add in the pos and relational features
        pos_feats = np.zeros((len(pos_ids), len(POS2ID)))
        pos_feats[range(len(pos_ids)), pos_ids] = 1
        rel_feats = np.zeros((len(rel_ids), len(REL2ID)))
        rel_feats[range(len(rel_ids)), rel_ids] = 1
        
        feats = np.concatenate((feats, pos_feats, rel_feats), axis=1)

        # add pad back in                
        feats = np.concatenate((feats, np.zeros((pad_len, feats.shape[1]))))

        return feats


    def featurize_batch(self, batch_ids, rel_ids, pos_ids, padded_len=0):
        """ takes [batch, len] returns [batch, len, features] """
        #print(rel_ids)
        #print(batch_ids)
        #print(pos_ids)
        batch_feats = [
            self.features(list(id_seq), list(rel_ids), list(pos_ids)) 
            for id_seq, rel_ids, pos_ids in zip(batch_ids, rel_ids, pos_ids)]
        batch_feats = np.array(batch_feats)
        return batch_feats

## Tokenizer and BERT initialization

In [2]:
# Import the tokenizer and BERT model via the transformers package
from transformers import BertTokenizer, BertModel

# Use a pretrained tokenizer
tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
tok2id = tokenizer.vocab
tok2id['<del>'] = len(tok2id)

# Use a pretrained BERT model
bertmodel = BertModel.from_pretrained("bert-base-uncased")

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


## MODULAR Detection Module

In [3]:
# Define the number of layers and hidden size, these are defined in the paper

layers = 12
hidden_size = 768

## TAKEN FROM GITHUB CODE OF NEUTRALIZING BIAS
## https://github.com/rpryzant/neutralizing-bias

class ConcatCombine(torch.nn.Module):
    def __init__(self, hidden_size, feature_size, out_size, layers,
            dropout_prob, small=False, pre_enrich=False, activation=False,
            include_categories=False, category_emb=False,
            add_category_emb=False):
        super(ConcatCombine, self).__init__()

        self.include_categories = include_categories
        self.add_category_emb = add_category_emb
        if include_categories:
            if category_emb and not add_category_emb:
                feature_size *= 2
            elif not category_emb:
                feature_size += 43

        if layers == 1:
            self.out = torch.nn.Sequential(
                torch.nn.Linear(hidden_size + feature_size, out_size),
                torch.nn.Dropout(dropout_prob))
        elif layers == 2:
            waist_size = min(hidden_size, feature_size) if small else max(hidden_size, feature_size)
            if activation:
                self.out = torch.nn.Sequential(
                    torch.nn.Linear(hidden_size + feature_size, waist_size),
                    torch.nn.Dropout(dropout_prob),
                    torch.nn.ReLU(),
                    torch.nn.Linear(waist_size, out_size),
                    torch.nn.Dropout(dropout_prob))
            else:
                self.out = torch.nn.Sequential(
                    torch.nn.Linear(hidden_size + feature_size, waist_size),
                    torch.nn.Dropout(dropout_prob),
                    torch.nn.Linear(waist_size, out_size),
                    torch.nn.Dropout(dropout_prob))
        if pre_enrich:
            if activation:
                self.enricher = torch.nn.Sequential(
                    torch.nn.Linear(feature_size, feature_size),
                    torch.nn.ReLU())
            else:
                self.enricher = torch.nn.Linear(feature_size, feature_size)
        else:
            self.enricher = None
        # manually set cuda because module doesn't see these combiners for bottom 
#         if CUDA:
#             self.out = self.out.cuda()
#             if self.enricher: 
#                 self.enricher = self.enricher.cuda()
                
    def forward(self, hidden, features, categories=None):
        if self.include_categories:
            categories = categories.unsqueeze(1)
            categories = categories.repeat(1, features.shape[1], 1)
            if self.add_category_emb:
                features = features + categories
            else:
                features = torch.cat((features, categories), -1)

        if self.enricher is not None:
            features = self.enricher(features)

        return self.out(torch.cat((hidden, features), dim=-1))
    

class BertDetector(torch.nn.Module):
    def __init__(self,cls_num_labels=2,token_num_labels=2,tok2id=None):
        super(BertDetector,self).__init__()
        self.bert = bertmodel
        self.featurizer = Featurizer(tok2id,lexicon_feature_bits=1)
        self.cls_dropout = torch.nn.Dropout(0.15)
        self.cls_classifier = torch.nn.Linear(hidden_size,cls_num_labels)
        
        self.token_dropout = torch.nn.Dropout(0.15)
        #self.token_classifier = torch.nn.Linear(hidden_size,token_num_labels)
        
        self.token_classifier = ConcatCombine(
                hidden_size, 90, token_num_labels, 
                1, 0, False, pre_enrich=False,
                activation=False,
                include_categories=False,
                category_emb=False,
                add_category_emb=False)
        
    def forward(self,input_ids,train=None,token_type_ids=None,attention_mask=None, 
        labels=None,rel_ids=None,pos_ids=None,categories=None,pre_len=None):
        features = torch.tensor(self.featurizer.featurize_batch(
            input_ids.numpy(), 
            rel_ids.numpy(), 
            pos_ids.numpy(), 
            padded_len=input_ids.shape[1]),dtype=torch.float)
        results = self.bert(input_ids)
        sequence = results.last_hidden_state
        pooled = results.pooler_output
        if train == "train":
            cls_logits = self.cls_dropout(self.cls_classifier(pooled))
            token_logits = self.token_dropout(self.token_classifier(sequence,features))
        else:
            cls_logits = self.cls_classifier(pooled)
            token_logits = self.token_classifier(sequence,features)
        return cls_logits,token_logits

## Token Generation and Detector Module Testing

In [4]:
# Example headline text
text_1 = "China vowed on Wednesday to \"fight back\" after the United States announced a possible second round of tariff hikes on $200 billion worth of Chinese goods. The U.S. proposal released on Tuesday included increased taxes on imported food products and consumer electronics."

# Encode the text into BERT tokens
indexed_tokens = tokenizer.encode(text_1, add_special_tokens=True)

# Convert these tokens to a Tensor
tokens_tensor = torch.tensor([indexed_tokens])

# Generate the segment tensors.  The 102 is the [SEP] token and multiple of these 
# The code here assumes there are at most two texts fed to the tokenized encoder.

# These tensors give each token an ID based on what text they belong to
lengths = (tokens_tensor == 102).nonzero(as_tuple=True)[1]
try: 
    segments_ids = [0] * (lengths[0] + 1) + [1] * (lengths[1] - lengths[0])
except:
    segments_ids = [0] * (lengths[0] + 1)
segments_tensors = torch.tensor([segments_ids])
segments_tensors

# Generate the relational and positional encoders.  This is present in the original GitHub code as part of the MODULAR algorithm.
# When the information is not available (e.g. in our own dataset), these are filled with <UNK> tokens
rel_tensor = torch.tensor([REL2ID[x] for x in ["<UNK>"]*len(indexed_tokens)])
pos_tensor = torch.tensor([POS2ID[x] for x in ["<UNK>"]*len(indexed_tokens)])

(tokens_tensor,segments_tensors,rel_tensor,pos_tensor)

(tensor([[  101,  2859, 18152,  2006,  9317,  2000,  1000,  2954,  2067,  1000,
           2044,  1996,  2142,  2163,  2623,  1037,  2825,  2117,  2461,  1997,
          23234, 21857,  2015,  2006,  1002,  3263,  4551,  4276,  1997,  2822,
           5350,  1012,  1996,  1057,  1012,  1055,  1012,  6378,  2207,  2006,
           9857,  2443,  3445,  7773,  2006, 10964,  2833,  3688,  1998,  7325,
           8139,  1012,   102]]),
 tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
          0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
          0, 0, 0, 0, 0]]),
 tensor([45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45,
         45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45,
         45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45, 45]),
 tensor([15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15,
         15, 15, 15, 15, 15, 15, 15, 15, 15, 15, 15,

In [5]:
# Create the BertDetector model
model = BertDetector(tok2id=tok2id)

# Generate results, these are in the form of a tuple where the first element returns values for just the [CLS] token
# and the second element returns values for everything else.
results = model(tokens_tensor,token_type_ids=segments_tensors,rel_ids=rel_tensor.unsqueeze(0),pos_ids=pos_tensor.unsqueeze(0))
(results,torch.nn.Softmax(dim=1)(results[1]))

((tensor([[-0.0517, -0.5244]], grad_fn=<AddmmBackward>),
  tensor([[[ 0.4846,  0.2814],
           [ 0.3863,  0.0817],
           [ 0.2775, -0.3158],
           [ 0.5077, -0.1507],
           [ 0.1739, -0.0308],
           [-0.1166, -0.1629],
           [ 0.0812, -0.3776],
           [-0.2618, -0.6185],
           [-0.0981, -0.3988],
           [ 0.4846,  0.0514],
           [ 0.4730, -0.0056],
           [ 0.5697, -0.3963],
           [ 0.5234, -0.2881],
           [ 0.6422, -0.1745],
           [ 0.3207, -0.4543],
           [ 0.1040, -0.0873],
           [-0.1369,  0.3556],
           [-0.0221, -0.0388],
           [-0.2431, -0.0989],
           [ 0.0042, -0.2524],
           [ 0.0117, -0.7513],
           [-0.3080, -0.4874],
           [-0.1520, -0.2115],
           [ 0.0286, -0.0834],
           [ 0.3734,  0.0252],
           [ 0.1491,  0.0577],
           [-0.0652,  0.1527],
           [-0.1598, -0.0655],
           [-0.3144, -0.3606],
           [-0.1854, -0.1669],
           [-

In [ ]:
# The following is more testing, but with additional functionality where specified

In [6]:
# Example headline text, taken directly from the WNC set
text_test= "165188319	ch ##lor ##of ##or ##m \" the molecular life ##sa ##ver \" an article at oxford university providing interesting facts about ch ##lor ##of ##or ##m .	ch ##lor ##of ##or ##m \" the molecular life ##sa ##ver \" an article at oxford university providing facts about ch ##lor ##of ##or ##m .	chloroform \"the molecular lifesaver\" an article at oxford university providing interesting facts about chloroform.	chloroform \"the molecular lifesaver\" an article at oxford university providing facts about chloroform.	NOUN NOUN NOUN NOUN NOUN PUNCT DET ADJ NOUN NOUN NOUN PUNCT DET NOUN ADP NOUN NOUN VERB ADJ NOUN ADP NOUN NOUN NOUN NOUN NOUN PUNCT	ROOT ROOT ROOT ROOT ROOT punct det amod dobj dobj dobj punct det appos prep compound pobj acl amod dobj prep pobj pobj pobj pobj pobj punct"

# Strip these texts into different components
[revid, _, _, biased, nonbiased, pos, rels] = text_test.strip().split("\t")

indexed_tokens = tokenizer.encode(biased.strip(),nonbiased.strip(), add_special_tokens=True)

tokens_tensor = torch.tensor([indexed_tokens])
lengths = (tokens_tensor == 102).nonzero(as_tuple=True)[1]
try: 
    segments_ids = [0] * (lengths[0] + 1) + [1] * (lengths[1] - lengths[0])
except:
    segments_ids = [0] * (lengths[0] + 1)
segments_tensors = torch.tensor([segments_ids])
segments_tensors


rel_tensor = torch.tensor([REL2ID[x] for x in rels.strip().split(" ")]*2)
pos_tensor = torch.tensor([POS2ID[x] for x in pos.strip().split(" ")]*2)

# Ensuring that all tensors are of the same size
while rel_tensor.size()[0] < len(indexed_tokens):
    rel_tensor = torch.cat((rel_tensor, torch.tensor([0])), dim=-1)
while pos_tensor.size()[0] < len(indexed_tokens):
    pos_tensor = torch.cat((pos_tensor, torch.tensor([0])), dim=-1)
    
# Generate a "ground truth" array of 1s and 0s where 1s indicate changes in tokens between the biased and nonbiased statements
ground_truth_list = [(x[0],len(x[1])) for x in diff(biased.strip().split(),nonbiased.strip().split())]
ground_truth = []
for i in ground_truth_list:
    if i[0] == "-":
        ground_truth.extend([1]*i[1])
    else:
        ground_truth.extend([0]*i[1])
ground_truth

(tokens_tensor,segments_tensors,rel_tensor,pos_tensor)

(tensor([[  101, 10381, 10626, 11253,  2953,  2213,  1000,  1996,  8382,  2166,
           3736,  6299,  1000,  2019,  3720,  2012,  4345,  2118,  4346,  5875,
           8866,  2055, 10381, 10626, 11253,  2953,  2213,  1012,   102, 10381,
          10626, 11253,  2953,  2213,  1000,  1996,  8382,  2166,  3736,  6299,
           1000,  2019,  3720,  2012,  4345,  2118,  4346,  8866,  2055, 10381,
          10626, 11253,  2953,  2213,  1012,   102]]),
 tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
          0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
          1, 1, 1, 1, 1, 1, 1, 1]]),
 tensor([ 5,  5,  5,  5,  5,  7,  0,  1, 14, 14, 14,  7,  0, 17,  3,  9,  4, 10,
          1, 14,  3,  4,  4,  4,  4,  4,  7,  5,  5,  5,  5,  5,  7,  0,  1, 14,
         14, 14,  7,  0, 17,  3,  9,  4, 10,  1, 14,  3,  4,  4,  4,  4,  4,  7,
          0,  0]),
 tensor([2, 2, 2, 2, 2, 6, 0, 1, 2, 2, 2, 6, 0, 2, 3, 2, 2, 5, 1, 2, 3, 2, 2, 2,
 

In [7]:
# Demonstration of the diff function

diff(biased.strip().split(),nonbiased.strip().split())

[('=',
  ['chloroform',
   '"the',
   'molecular',
   'lifesaver"',
   'an',
   'article',
   'at',
   'oxford',
   'university',
   'providing']),
 ('-', ['interesting']),
 ('=', ['facts', 'about', 'chloroform.'])]

In [9]:
model = BertDetector(tok2id=tok2id)
results = model(tokens_tensor,token_type_ids=segments_tensors,rel_ids=rel_tensor.unsqueeze(0),pos_ids=pos_tensor.unsqueeze(0))
(results,torch.nn.Softmax(dim=1)(results[1]),torch.argmax(torch.nn.Softmax(dim=1)(results[1]),dim=-1))

((tensor([[ 0.1812, -0.2723]], grad_fn=<AddmmBackward>),
  tensor([[[-0.6615,  0.1716],
           [-0.2087,  0.2696],
           [-0.4593, -0.0786],
           [ 0.1960, -0.6619],
           [-0.5898,  0.0152],
           [-0.4499, -0.0224],
           [-0.1283, -0.2362],
           [-0.4974, -0.1788],
           [-0.3294, -0.4225],
           [-0.0648, -0.2173],
           [ 0.4301, -0.2815],
           [ 0.2340, -0.3602],
           [-0.0687, -0.1605],
           [ 0.0427, -0.3235],
           [-0.0901, -0.3714],
           [ 0.2663, -0.3083],
           [-0.1482, -0.1498],
           [ 0.1569,  0.2401],
           [ 0.2422, -0.3405],
           [-0.0475, -0.4424],
           [-0.1028, -0.2259],
           [-0.1633, -0.5786],
           [ 0.0893, -0.5959],
           [-0.2626, -0.3703],
           [ 0.3370, -0.8774],
           [-0.4027, -0.2592],
           [-0.3603, -0.5741],
           [-0.4923, -0.6132],
           [ 0.2358, -0.2823],
           [ 0.0046, -0.4434],
           [-

## TRAINING

In [11]:
# Due to time constraints, the following code is designed to run for only one epoch.

# Read the training file
f = open("biased.word.train",encoding="utf-8")
i = 0

# Create the model and crossentropy loss funcction
model = BertDetector(tok2id=tok2id)
weights = torch.ones(2)
weights[-1] = 0
celossfn = torch.nn.CrossEntropyLoss(weight=weights)
softmax = torch.nn.Softmax(dim=-1)

# Create the Adam Optimizer, the learning rate is 1e-4
optimizer = torch.optim.Adam(model.parameters(),lr=0.0001)

for line in f:
    # Read the line data of the WNC dataset
    linedata = line.strip().split('\t')
    
    # Read in all the lines.  Some lines may not have positional or relational information.
    if len(linedata) == 7:
        [revid, biased2, nonbiased2, biased, nonbiased, pos, rels] = linedata
        indexed_tokens = tokenizer.encode(biased2.strip().replace(" ##",""), add_special_tokens=True)
    elif len(linedata) == 5:
        [revid, biased2, nonbiased2, biased, nonbiased] = linedata
        indexed_tokens = tokenizer.encode(biased2.strip().replace(" ##",""), add_special_tokens=True)
        pos = ["<UNK>"]*len(indexed_tokens)
        rels = ["<UNK>"]*len(indexed_tokens)
    else:
        continue
    
    # Create the tensors and the ground truth list
    tokens_tensor = torch.tensor([indexed_tokens])
    lengths = (tokens_tensor == 102).nonzero(as_tuple=True)[1]
    try: 
        segments_ids = [0] * (lengths[0] + 1) + [1] * (lengths[1] - lengths[0])
    except:
        segments_ids = [0] * (lengths[0] + 1)
    segments_tensors = torch.tensor([segments_ids])
    rel_tensor = torch.tensor([REL2ID[x] for x in rels.strip().split(" ")])
    pos_tensor = torch.tensor([POS2ID[x] for x in pos.strip().split(" ")])
    while rel_tensor.size()[0] < len(indexed_tokens):
        rel_tensor = torch.cat((rel_tensor, torch.tensor([0])), dim=-1)
    while pos_tensor.size()[0] < len(indexed_tokens):
        pos_tensor = torch.cat((pos_tensor, torch.tensor([0])), dim=-1)

    ground_truth_list = [(x[0],len(x[1])) for x in diff(biased2.strip().split(),nonbiased2.strip().split())]
    ground_truth = []
    for j in ground_truth_list:
        if j[0] == "-":
            ground_truth.extend([1]*j[1])
        elif j[0] == "=":
            ground_truth.extend([0]*j[1])
    
    i = i + 1
    
    # Obtain the token logits from the detection model
    results = model(tokens_tensor,train="train",token_type_ids=segments_tensors,rel_ids=rel_tensor.unsqueeze(0),pos_ids=pos_tensor.unsqueeze(0))
    _,token_logits = results
    
    # Calculate the loss and optimize it.  After several rounds of testing, this loss appears to have a consistent floor of 0.3133 even after testing other learning rates
    optimizer.zero_grad()
    while len(ground_truth) + 2 < len(softmax(token_logits)[0]):
        ground_truth.extend([0])
    loss = celossfn(softmax(token_logits)[0],torch.Tensor([0] + ground_truth + [0]).type('torch.LongTensor'))
    loss.backward()
    optimizer.step()
    
    if i % 10 == 0:
        print("Line: " + str(i))
        print(loss)
        print(" ")
        #break
#     if i >= 10000:
#         break
    
f.close()

Line: 10
tensor(0.3227, grad_fn=<NllLossBackward>)
 
Line: 20
tensor(0.3706, grad_fn=<NllLossBackward>)
 
Line: 30
tensor(0.3134, grad_fn=<NllLossBackward>)
 
Line: 40
tensor(0.3135, grad_fn=<NllLossBackward>)
 
Line: 50
tensor(0.3349, grad_fn=<NllLossBackward>)
 
Line: 60
tensor(0.3134, grad_fn=<NllLossBackward>)
 
Line: 70
tensor(0.3134, grad_fn=<NllLossBackward>)
 
Line: 80
tensor(0.3312, grad_fn=<NllLossBackward>)
 
Line: 90
tensor(0.3135, grad_fn=<NllLossBackward>)
 
Line: 100
tensor(0.3315, grad_fn=<NllLossBackward>)
 
Line: 110
tensor(0.3234, grad_fn=<NllLossBackward>)
 
Line: 120
tensor(0.3249, grad_fn=<NllLossBackward>)
 
Line: 130
tensor(0.3240, grad_fn=<NllLossBackward>)
 
Line: 140
tensor(0.3231, grad_fn=<NllLossBackward>)
 
Line: 150
tensor(0.3133, grad_fn=<NllLossBackward>)
 
Line: 160
tensor(0.3245, grad_fn=<NllLossBackward>)
 
Line: 170
tensor(0.3513, grad_fn=<NllLossBackward>)
 
Line: 180
tensor(0.3228, grad_fn=<NllLossBackward>)
 
Line: 190
tensor(0.3398, grad_fn=<Nll

## TESTING

In [252]:
# Individual Testing

# Replace biased2 with any potential headline
biased2 = "ali once dated american actor jonathan brandis who unfortunately died in 2003."
indexed_tokens = tokenizer.encode(biased2.strip().replace(" ##",""), add_special_tokens=True)
pos = " ".join(["<UNK>"]*len(indexed_tokens))
rels = " ".join(["<UNK>"]*len(indexed_tokens))

tokens_tensor = torch.tensor([indexed_tokens])
lengths = (tokens_tensor == 102).nonzero(as_tuple=True)[1]
try: 
    segments_ids = [0] * (lengths[0] + 1) + [1] * (lengths[1] - lengths[0])
except:
    segments_ids = [0] * (lengths[0] + 1)
segments_tensors = torch.tensor([segments_ids])
rel_tensor = torch.tensor([REL2ID[x] for x in rels.strip().split(" ")])
pos_tensor = torch.tensor([POS2ID[x] for x in pos.strip().split(" ")])
while rel_tensor.size()[0] < len(indexed_tokens):
    rel_tensor = torch.cat((rel_tensor, torch.tensor([0])), dim=-1)
while pos_tensor.size()[0] < len(indexed_tokens):
    pos_tensor = torch.cat((pos_tensor, torch.tensor([0])), dim=-1)

results = model(tokens_tensor,train="test",token_type_ids=segments_tensors,rel_ids=rel_tensor.unsqueeze(0),pos_ids=pos_tensor.unsqueeze(0))
_,token_logits = results

results

(tensor([[-0.1225,  0.3789]], grad_fn=<AddmmBackward>),
 tensor([[[ 12.0634, -12.1620],
          [ 12.0668, -12.1594],
          [ 12.0700, -12.1705],
          [ 12.0748, -12.1656],
          [ 12.0486, -12.1697],
          [ 12.0788, -12.1621],
          [ 12.0742, -12.1658],
          [ 12.0628, -12.1886],
          [ 12.0657, -12.1913],
          [ 12.0603, -12.1964],
          [ 12.0568, -12.1761],
          [ 12.0637, -12.2012],
          [ 12.0964, -12.2342],
          [ 12.0541, -12.1248],
          [ 12.0414, -12.1152],
          [ 12.0532, -12.1487]]], grad_fn=<AddBackward0>))

In [253]:
# Obtain the list of softmaxed values
index = softmax(token_logits)[:,:,1][0][1:-1].detach().numpy()

# Obtain the token with the most potential bias
idx = np.argmax(index)

(idx, np.max(index), index, (index-np.min(index))/(np.max(index)-np.min(index)))

(13,
 3.2278246e-11,
 array([3.0110286e-11, 2.9683582e-11, 2.9684488e-11, 3.0347252e-11,
        2.9669545e-11, 2.9696436e-11, 2.9360316e-11, 2.9194355e-11,
        2.9205829e-11, 2.9908690e-11, 2.8967826e-11, 2.7124141e-11,
        3.1566205e-11, 3.2278246e-11], dtype=float32),
 array([0.5793721 , 0.49658296, 0.49675864, 0.6253484 , 0.49385944,
        0.49907696, 0.4338629 , 0.40166312, 0.4038892 , 0.54025847,
        0.35771197, 0.        , 0.8618496 , 1.        ], dtype=float32))

In [198]:
# Normalize the array so that the most biased word is "1" and the least biased word is "0".  These would be the probabilities.
normindex = (index-np.min(index))/(np.max(index)-np.min(index))

# Print a tuple containing the token, the token with surrounding tokens to provide context, the softmax logit value, and the probability value
for idx in np.flip(np.argsort(index)):
    print((tokenizer.decode(indexed_tokens[idx+1:idx+2]),tokenizer.decode(indexed_tokens[idx:idx+3]),index[idx],normindex[idx]))

('.', '2003. [SEP]', 3.2278246e-11, 1.0)
('2003', 'in 2003.', 3.1566205e-11, 0.8618496)
('american', 'dated american actor', 3.0347252e-11, 0.6253484)
('ali', '[CLS] ali once', 3.0110286e-11, 0.5793721)
('unfortunately', 'who unfortunately died', 2.990869e-11, 0.54025847)
('jonathan', 'actor jonathan brand', 2.9696436e-11, 0.49907696)
('dated', 'once dated american', 2.9684488e-11, 0.49675864)
('once', 'ali once dated', 2.9683582e-11, 0.49658296)
('actor', 'american actor jonathan', 2.9669545e-11, 0.49385944)
('brand', 'jonathan brandis', 2.9360316e-11, 0.4338629)
('who', '##is who unfortunately', 2.920583e-11, 0.4038892)
('##is', 'brandis who', 2.9194355e-11, 0.40166312)
('died', 'unfortunately died in', 2.8967826e-11, 0.35771197)
('in', 'died in 2003', 2.7124141e-11, 0.0)


In [265]:
import pandas as pd
testset = pd.read_csv("newdataset_withBias.csv")["text"].to_numpy()

randintlist = []
textlist = []
tupleslist = []

w = 0
for w in range(len(testset)):
    print(w)

    #randint = np.random.randint(0,len(testset))
    #randint = 32122
    
    randint = w
    biased2 = testset[randint]
    if biased2 == "":
        randintlist.append(randint)
        textlist.append(testset[randint])
        tupleslist.append([])
        print("err")
        continue
    
    #punctuation = '''!()-[]{};:'"\,<>./?@#$%^&*_~'''
    #for punc in punctuation:
    #    biased2 = biased2.replace(punc,"")
    
    try :
        indexed_tokens = tokenizer.encode(biased2.strip().replace(" ##",""), add_special_tokens=True)
    except:
        randintlist.append(randint)
        textlist.append(testset[randint])
        tupleslist.append([])
        print("err")
        continue
    pos = " ".join(["<UNK>"]*len(indexed_tokens))
    rels = " ".join(["<UNK>"]*len(indexed_tokens))

    tokens_tensor = torch.tensor([indexed_tokens])
    lengths = (tokens_tensor == 102).nonzero(as_tuple=True)[1]
    try: 
        segments_ids = [0] * (lengths[0] + 1) + [1] * (lengths[1] - lengths[0])
    except:
        segments_ids = [0] * (lengths[0] + 1)
    segments_tensors = torch.tensor([segments_ids])
    rel_tensor = torch.tensor([REL2ID[x] for x in rels.strip().split(" ")])
    pos_tensor = torch.tensor([POS2ID[x] for x in pos.strip().split(" ")])
    while rel_tensor.size()[0] < len(indexed_tokens):
        rel_tensor = torch.cat((rel_tensor, torch.tensor([0])), dim=-1)
    while pos_tensor.size()[0] < len(indexed_tokens):
        pos_tensor = torch.cat((pos_tensor, torch.tensor([0])), dim=-1)

    i = i + 1

    results = model(tokens_tensor,train="test",token_type_ids=segments_tensors,rel_ids=rel_tensor.unsqueeze(0),pos_ids=pos_tensor.unsqueeze(0))
    _,token_logits = results

    results
    index = softmax(token_logits)[:,:,1][0][1:-1].detach().numpy()
    idx = np.argmax(index)
    (idx, tokenizer.decode(indexed_tokens[idx:idx+3]), np.max(index), index, (index-np.min(index))/(np.max(index)-np.min(index)))

    randintlist.append(randint)
    textlist.append(testset[randint])
    tupleslistsub = []
    normindex = (index-np.min(index))/(np.max(index)-np.min(index))
    for idx in np.flip(np.argsort(index)):
        tupleslistsub.append((tokenizer.decode(indexed_tokens[idx+1:idx+2]),tokenizer.decode(indexed_tokens[idx:idx+3]),index[idx],normindex[idx]))
    tupleslist.append(tupleslistsub)

0
1
2
3
err
4
5
6
7
8
9
10
err
11
12
13
14
15
16
17
18
err
19
20
21
22
23
24
25
26
27
28
err
29
30
31
err
32
err
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
err
57
58
err
59
60
61
62
63
err
64
65
66
err
67
68
69
70
71
72
73
74
err
75
76
77
78
79
80
81
82
83
84
85
err
86
87
88
89
90
91
92
93
94
95
96
err
97
98
99
100
101
102
103
err
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
err
124
125
126
127
128
129
130
131
132
err
133
134
135
136
err
137
138
139
140
141
142
143
144
145
146
147
148
149
150
err
151
152
153
154
err
155
156
157
158
159
160
161
162
163
164
165
err
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
err
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
err
224
225
226
227
228
err
229
230
231
232
233
234
235
236
237
238
err
239
err
240
241
242
243
244
245
246
247
248
249
250
251
25

RuntimeError: The expanded size of the tensor (974) must match the existing size (512) at non-singleton dimension 1.  Target sizes: [1, 974].  Tensor sizes: [1, 512]

In [266]:
(randintlist, textlist, tupleslist)

([0,
  1,
  2,
  3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21,
  22,
  23,
  24,
  25,
  26,
  27,
  28,
  29,
  30,
  31,
  32,
  33,
  34,
  35,
  36,
  37,
  38,
  39,
  40,
  41,
  42,
  43,
  44,
  45,
  46,
  47,
  48,
  49,
  50,
  51,
  52,
  53,
  54,
  55,
  56,
  57,
  58,
  59,
  60,
  61,
  62,
  63,
  64,
  65,
  66,
  67,
  68,
  69,
  70,
  71,
  72,
  73,
  74,
  75,
  76,
  77,
  78,
  79,
  80,
  81,
  82,
  83,
  84,
  85,
  86,
  87,
  88,
  89,
  90,
  91,
  92,
  93,
  94,
  95,
  96,
  97,
  98,
  99,
  100,
  101,
  102,
  103,
  104,
  105,
  106,
  107,
  108,
  109,
  110,
  111,
  112,
  113,
  114,
  115,
  116,
  117,
  118,
  119,
  120,
  121,
  122,
  123,
  124,
  125,
  126,
  127,
  128,
  129,
  130,
  131,
  132,
  133,
  134,
  135,
  136,
  137,
  138,
  139,
  140,
  141,
  142,
  143,
  144,
  145,
  146,
  147,
  148,
  149,
  150,
  151,
  152,
  153,
  154,
  155,
  156,
  157,
  15

In [267]:
df = pd.DataFrame(randintlist)
df["og_text"] = textlist
df["tuples"] = tupleslist
#df.to_csv("BiasedWordIdentificationTableRun1.csv")

In [268]:
df

0                                            og_text  \
0        0  During last night's debut of the HBO documenta...   
1        1  Eugene Vodolazkin's Laurus was a finalist for ...   
2        2  By JOHN HABIB New Hampshire Union Leader May 0...   
3        3                                                NaN   
4        4  China vowed on Wednesday to "fight back" after...   
...    ...                                                ...   
9432  9432  Sen. Bernie Sanders at a rally in Washington S...   
9433  9433  Andrew Zimmern is the host of Bizarre Foods on...   
9434  9434  Video | Ammoland Inc. Posted on January 11, 20...   
9435  9435  THE 20 top blackspots for jobless young Briton...   
9436  9436  Despite controversies that rage over immigrati...   

                                                 tuples  
0     [(her, with her was, 3.3467663e-11, 1.0), (was...  
1     [(,, novel, translated, 3.2455545e-11, 1.0), (...  
2     [(high, trinity high who, 3.3149754e-11, 1.0),...  
3                                                    []  
4     [(200, $ 200 billion, 3.293334e-11, 1.0), (chi...  
...                                                 ...  
9432  [(new, in new york, 3.301529e-11, 1.0), (prima...  
9433  [(good, pretty good show, 3.260732e-11, 1.0), ...  
9434  [(white, the white house, 3.338873e-11, 1.0), ...  
9435  [(year, 24 year -, 3.2414963e-11, 1.0), (three...  
9436  [(against, or against immigrants, 3.2999298e-1...  

[9437 rows x 3 columns]

In [274]:
df.to_csv("BiasedWordIdentificationTableRun.csv")

In [275]:
index = softmax(token_logits)[:,:,1][0][1:-1].detach().numpy()
idx = np.argmax(index)
(idx, tokenizer.decode(indexed_tokens[idx:idx+3]), np.max(index), index, (index-np.min(index))/(np.max(index)-np.min(index)))

(19,
 'trump administration expands',
 3.2999298e-11,
 array([3.0669859e-11, 2.9138445e-11, 2.9151955e-11, 2.8146123e-11,
        2.9492270e-11, 2.9543559e-11, 3.0014186e-11, 2.8992590e-11,
        3.1063600e-11, 3.0656758e-11, 2.8964954e-11, 2.5694341e-11,
        3.1181609e-11, 3.1160564e-11, 2.9576938e-11, 3.1047370e-11,
        3.1087664e-11, 2.7589937e-11, 3.1865340e-11, 3.2999298e-11,
        3.1361861e-11, 2.7188111e-11, 3.2420899e-11, 3.1780363e-11,
        2.9648669e-11, 3.0035030e-11, 3.0070970e-11, 3.0031019e-11,
        2.9992439e-11, 3.0021284e-11, 3.2151056e-11, 3.1745648e-11,
        2.7536418e-11, 3.2423619e-11, 3.1879808e-11], dtype=float32),
 array([0.6811153 , 0.47147498, 0.4733244 , 0.33563262, 0.5199112 ,
        0.5269323 , 0.591358  , 0.4515083 , 0.7350158 , 0.67932194,
        0.44772515, 0.        , 0.7511706 , 0.7482895 , 0.53150177,
        0.73279405, 0.73831004, 0.25949454, 0.84476876, 1.        ,
        0.7758458 , 0.20448722, 0.92082113, 0.83313596, 0.54

In [276]:
print(w)
print(testset[w])
normindex = (index-np.min(index))/(np.max(index)-np.min(index))
for idx in np.flip(np.argsort(index)):
    print((tokenizer.decode(indexed_tokens[idx+1:idx+2]),tokenizer.decode(indexed_tokens[idx:idx+3]),index[idx],normindex[idx]))

9437
The Left Admits Americans Want Opportunities Not Handouts July 30 2018 by Patrice Lee Onwuka
Trump Administration Expands Cheaper, Quality Healthcare Plans June 20 2018 by Patrice Lee Onwuka
Hysteria Comes to Black Hair Care Products - Again May 16 2018 by Patrice Lee Onwuka
On Mother's Day, Advice from Some Moms May 12 2018 by Patrice Lee Onwuka
Tennis Star Venus Williams Rejects "Feminist" Label May 10 2018 by Patrice Lee Onwuka
Nancy Pelosi Chokes on "Crumbs" Comments April 25 2018 by Patrice Lee Onwuka
Google Shares How It Closed Unexplained Pay Gaps March 20 2018 by Patrice Lee Onwuka
DeVos Backlash Incites Dangerous Language September 14 2017 by Patrice Lee Onwuka
Kim Kardashian Still Eschews One Label: Feminist September 5 2017 by Patrice Lee Onwuka
Jerry Springer Rides the $15 Minimum Wage Wagon September 5 2017 by Patrice Lee Onwuka
No, Melania's Shoes are Not the Story, Texas is August 30 2017 by Patrice Lee Onwuka
Amy Schumer's Equal Pay Problem August 25 2017 by Patric